In [22]:
import pandas as pd
from sklearn.model_selection import train_test_split
import torch
import torch.nn as nn

torch.manual_seed(0)

In [23]:
data=pd.read_csv('YearPredictionMSD.csv',nrows=50000,header=None)
print(data.head())
print(data.shape)

     0         1         2         3         4         5         6         7   \
0  2001  49.94357  21.47114  73.07750   8.74861 -17.40628 -13.09905 -25.01202   
1  2001  48.73215  18.42930  70.32679  12.94636 -10.32437 -24.83777   8.76630   
2  2001  50.95714  31.85602  55.81851  13.41693  -6.57898 -18.54940  -3.27872   
3  2001  48.24750  -1.89837  36.29772   2.58776   0.97170 -26.21683   5.05097   
4  2001  50.97020  42.20998  67.09964   8.46791 -15.85279 -16.81409 -12.48207   

         8         9   ...        81         82        83        84        85  \
0 -12.23257   7.83089  ...  13.01620  -54.40548  58.99367  15.37344   1.11144   
1  -0.92019  18.76548  ...   5.66812  -19.68073  33.04964  42.87836  -9.90378   
2  -2.35035  16.07017  ...   3.03800   26.05866 -50.92779  10.93792  -0.07568   
3 -10.34124   3.55005  ...  34.57337 -171.70734 -16.96705 -46.67617 -12.51516   
4  -9.37636  12.63699  ...   9.92661  -55.95724  64.92712 -17.72522  -1.49237   

         86         87    

In [24]:
cols=data.columns  # data數據集的所有行數
num_cols=data._get_numeric_data().columns  # data數據集中所有為數值型態的行數
print(list(set(cols)-set(num_cols)))

[]


In [25]:
print(data.isnull().sum().sum())

0


In [26]:
outliers=[]
for i in range(data.shape[1]):
    min_t=data[data.columns[i]].mean()-(3*data[data.columns[i]].std())
    max_t=data[data.columns[i]].mean()+(3*data[data.columns[i]].std())
    count=0
    for j in data[data.columns[i]]:
        if j<min_t or j>max_t:
            count += 1
    percentage=count/data.shape[0]
    #print(i, percentage)
    if percentage > 0.05:
        outliers.append(i)

print(outliers)

[]


In [27]:
x=data.iloc[:,1:]
y=data.iloc[:,0]

In [28]:
x=(x-x.mean())/x.std()
print(x.head())

         1         2         3         4         5         6         7   \
0  1.082657  0.382437  1.841985  0.459652 -0.480074 -0.282606 -1.590785   
1  0.880874  0.321953  1.763666  0.717085 -0.165507 -1.188896  0.777905   
2  1.251484  0.588929  1.350579  0.745944  0.000857 -0.703401 -0.066747   
3  0.800148 -0.082240  0.794774  0.081829  0.336246 -1.295366  0.517369   
4  1.253660  0.794806  1.671781  0.442438 -0.411071 -0.569426 -0.712128   

         8         9         10  ...        81        82        83        84  \
0 -1.300854  0.378336 -0.683719  ... -0.086005  0.099339  0.148291 -0.255625   
1  0.122576  1.420531  0.401198  ... -0.316635  0.301448 -0.063611  0.031855   
2 -0.057380  1.163637 -0.090081  ... -0.399185  0.567666 -0.749508 -0.301984   
3 -1.062869 -0.029679 -1.282306  ...  0.590596 -0.583396 -0.472129 -0.904164   
4 -0.941459  0.836414 -0.160630  ... -0.182976  0.090307  0.196753 -0.601570   

         85        86        87        88        89        90  
0  0

In [29]:
# 拆分數據成2個子集，x_new : x_test = 80:20
x_new, x_test, y_new, y_test=train_test_split(x, y, test_size=0.2, random_state=0)

# 再拆分數據集x_new成2個子集, x_train : x_dev = 75:25
x_train, x_dev, y_train, y_dev=train_test_split(x_new, y_new, test_size=0.25, random_state=0)

print(x_train.shape, x_dev.shape, x_test.shape)

(30000, 90) (10000, 90) (10000, 90)


In [30]:
x_train_torch=torch.tensor(x_train.values).float()
y_train_torch=torch.tensor(y_train.values).float().unsqueeze(1)
x_dev_torch=torch.tensor(x_dev.values).float()
y_dev_torch=torch.tensor(y_dev.values).float().unsqueeze(1)
x_test_torch=torch.tensor(x_test.values).float()
y_test_torch=torch.tensor(y_test.values).float().unsqueeze(1)

print(x_train_torch.shape, y_train_torch.shape)


torch.Size([30000, 90]) torch.Size([30000, 1])


In [31]:
model=nn.Sequential(
    nn.Linear(x_train.shape[1],200),
    nn.ReLU(),
    nn.Linear(200,50),
    nn.ReLU(),
    nn.Linear(50,1)
)

In [32]:
'''
device="cuda"
model=model.to(device)
x_train_torch=x_train_torch.to(device)
y_train_torch=y_train_torch.to(device)
x_dev_torch=x_dev_torch.to(device)
y_dev_torch=y_dev_torch.to(device)
'''

'\ndevice="cuda"\nmodel=model.to(device)\nx_train_torch=x_train_torch.to(device)\ny_train_torch=y_train_torch.to(device)\nx_dev_torch=x_dev_torch.to(device)\ny_dev_torch=y_dev_torch.to(device)\n'

In [33]:
myloss=torch.nn.MSELoss()
optimizer=torch.optim.Adam(model.parameters(),lr=0.01)

In [34]:
epochs=5001
for epoch in range(epochs):
    model.train()
    y_pred=model(x_train_torch)
    train_loss=myloss(y_pred,y_train_torch)
    optimizer.zero_grad()
    train_loss.backward()
    optimizer.step()

    if (epoch%400==0):
        with torch.no_grad():
            model.eval()
            y_pred2=model(x_dev_torch)
            valid_loss=myloss(y_pred2,y_dev_torch)

        print(f"epoch={epoch},  train_loss:{train_loss.item():.3f},valid_loss:{valid_loss.item():.3f}")

        if train_loss.item() < 81:
            break


epoch=0,  train_loss:3994186.750,valid_loss:3991035.000
epoch=400,  train_loss:8712.208,valid_loss:12554.796
epoch=800,  train_loss:279.507,valid_loss:782.861
epoch=1200,  train_loss:113.957,valid_loss:384.478
epoch=1600,  train_loss:90.560,valid_loss:293.845
epoch=2000,  train_loss:83.804,valid_loss:259.091
epoch=2400,  train_loss:171.167,valid_loss:318.227
epoch=2800,  train_loss:94.999,valid_loss:278.946
epoch=3200,  train_loss:94.926,valid_loss:244.094
epoch=3600,  train_loss:145.176,valid_loss:266.328
epoch=4000,  train_loss:291.952,valid_loss:465.639
epoch=4400,  train_loss:77.721,valid_loss:236.657


In [35]:
model=model.to("cpu")
pred=model(x_test_torch)
test_loss=myloss(pred,y_test_torch)
print(f"test_loss: {test_loss.item():.3f}")

test_loss: 357.332


In [36]:
for i in range(100,110):
    print(f"truth:{y_test_torch[i].item():.0f}, pred:{pred[i].item():.0f}")

truth:2006, pred:2010
truth:2003, pred:1998
truth:2002, pred:2000
truth:2005, pred:2098
truth:2007, pred:2001
truth:2008, pred:2001
truth:2001, pred:2004
truth:2006, pred:2003
truth:2008, pred:2007
truth:1966, pred:1989
